## Inserting Data Lab Content into Organizer Topics

Data Lab Functions can be used to insert Data Lab content directly into Organizer Topic.  Data Lab Functions use the cells in a Jupyter Notebook as an API endpoint. 

## How To Define A Data Lab Functions Notebook
### Notebook Cells
#### Context Cell

- A notebook cell that is not decorated with a top-line comment resembling a RESTful endpoint. Context cells appear sequentially at the beginning of a Jupyter notebook and are executed only once in a new kernel.

#### Endpoint Cell

- A notebook cell that is decorated with a top-line comment resembling a RESTful endpoint. For example:

```
# GET /items
items = spy.search({
    'Path': 'Example >> Cooling Tower 1 >> Area A',
    'Name': 'Compressor'
})
items.to_json()
```

- Endpoint cells must appear after context cells in a Jupyter notebook

- Allowed HTTP methods are GET, POST, PATCH, PUT, DELETE

- Endpoints can include nested paths. For example, # GET /items/area-a/compressor

- Endpoints do not support path parameters. Instead, both query parameters and a request body are available in the REQUEST object which is instantiated in the kernel for every Data Lab Functions request.

- Endpoint cells must be unique. That is, they cannot duplicate HTTP method + endpoint name

- Endpoint cell response content-types

    - application/json (default)

        - Cell response should be Python objects or literals. Data Lab Functions responses performs json.dumps() on endpoint cell output.

    - image/*

    - text/plain

    - text/html
`
### Reserved Variables
#### REQUEST

On each request, Data Lab Functions injects a REQUEST variable of type Dict directly into the kernel. The REQUEST dictionary contains all the relevant HTTP Request information, namely:

| REQUEST Variable | Type | Description |
| --- | --- ||
|info | Dict||
|id|str| Unique ID of the request|
|user_id|str| The Seeq user UUID invoking the request|
|notebook |str| The path and name of the API notebook|
|method| str |HTTP method|
|endpoint|str| Endpoint name|
|body|str/Dict|Parsed from JSON or Form-Encoded name-value pairs|
|args|Dict|Parsed query string name-value pairs |
|headers|Dict|HTTP Header name-value pairs |



An example url for an endpoint in this notebook would look like this.

### An optional common definition that could be called by various endpoints

In [1]:
from io import StringIO
import plotly.express as px

#def get_query_params(*names):
#    args = REQUEST['args']
#    return {name: args.get(name, None) for name in names}

def fig_to_html(fig):
    buffer = StringIO()
    fig.write_html(buffer, full_html=True, include_plotlyjs=True)
    return {'headers': {'Content-Type': 'text/html'}, 'data': buffer.getvalue()}

## Insert Static Content

In [ ]:
# GET /static_image
# data-lab/<GUID>/functions/notebooks/exampleR62/endpoints/static_image
import plotly.graph_objects as go

fig = go.Figure(go.Indicator(
    mode = "gauge+number",
    value = 450,
    title = {'text': "Speed"},
    domain = {'x': [0, 1], 'y': [0, 1]}
))

#{'headers': {'Content-Type': 'text/html'}, 'data': fig.to_html()}
fig_to_html(fig)

## Insert Dynamic Text that displays recent signal value

In [ ]:
# GET /text_string
# Update the URL from this project into the partial link below, then use that 
#  in the URL entry field in Organizer (excluding the #)
#  data-lab/<GUID>/functions/notebooks/exampleR62/endpoints/text_string

import rich
from seeq import spy
from rich.console import Console
from rich.text import Text
from datetime import datetime, timedelta

console = Console()

#Current time - timezone struggles so this shifts "now" to have data not NAN at the end of the df
current_datetime=datetime.now()-timedelta(hours=8)
#1 hr earlier
hour_prior=current_datetime - timedelta(hours=10)
#find string signal you want to display in Organizer
signal=spy.search({'Name':'Area A_Compressor Stage','Datasource Name':'Example Data'})
#pull data for representative time frame
data=spy.pull(signal,start=hour_prior, end=current_datetime,grid='1h',tz_convert='UTC')

# Get the dataframe's last row of text for the signal displayed
last_row_text = Text(data['Area A_Compressor Stage'].iloc[-1])

# Print that strig with bold formatting
console.print(last_row_text, style="bold" )